#Let's visualise data with Folium library!

__Folium -> https://github.com/python-visualization/folium__

In [1]:
import folium

##The dataset: Severe Acute Malnutrition (SAM) in Sahel

__Dataset__: https://data.hdx.rwlabs.org/dataset/prevalence-of-severe-acute-malnutrition-of-sahel

__Description__: 
The dataset represents the latest Severe Acute Malnutrition Prevalence available from 2010 to 2015 for the Sahel nine countries (Burkina Faso, Cameroon, Chad, the Gambia, Mali, Mauritania, Niger, Nigeria, Senegal).

__Note__: More on SAM here: http://globalnutritionreport.org/2014/08/13/measuring-the-burden-of-severe-acute-malnutrition/

In [2]:
from pandas import read_excel

import xlrd

In [3]:
df_sahel = read_excel("Sahel_Countries_SAM_Nutrition_Admin1_Summary_Latest_Surveys.xlsx")

In [4]:
df_sahel.head()

CNTRY_NAME CNTRY_CODE          ADM1_NAME ADM1_CODE Rowcacode1  \
0  Burkina Faso        BFA  Boucle du Mouhoun    BFA046     BFA046   
1  Burkina Faso        BFA           Cascades    BFA047     BFA047   
2  Burkina Faso        BFA             Centre    BFA013     BFA013   
3  Burkina Faso        BFA         Centre-Est    BFA048     BFA048   
4  Burkina Faso        BFA        Centre-Nord    BFA049     BFA049   

         Season  Year                                   Survey name  \
0  Post-Harvest  2014  Nutrition Survey SMART - Preliminary results   
1  Post-Harvest  2014  Nutrition Survey SMART - Preliminary results   
2  Post-Harvest  2013                        Nutrition Survey SMART   
3  Post-Harvest  2014  Nutrition Survey SMART - Preliminary results   
4  Post-Harvest  2014  Nutrition Survey SMART - Preliminary results   

                                            Comments  Latest SAM Prevalence  
0  Data collection Sept-Oct 2014 (Attention P/T a...                    1.4  
1  Data collection Sept-Oct 2014 (Attention P/T a...                    0.2  
2  Data collection Septembre 2013 (Attention P/T ...                    1.8  
3  Data collection Sept-Oct 2014 (Attention P/T a...                    1.0  
4  Data collection Sept-Oct 2014 (Attention P/T a...                    1.0

In [5]:
sahel_locations = [" ".join([df_sahel["ADM1_NAME"][i], df_sahel["CNTRY_NAME"][i]]) for i in range(len(df_sahel))]

sahel_locations[:5]

[u'Boucle du Mouhoun Burkina Faso',
 u'Cascades Burkina Faso',
 u'Centre Burkina Faso',
 u'Centre-Est Burkina Faso',
 u'Centre-Nord Burkina Faso']

In [6]:
## I need coordinates -> let's geocode with GeoPy!

In [7]:
from geopy.geocoders import Nominatim

g = Nominatim()

In [9]:
sahel_coord = [g.geocode(l) for l in sahel_locations]

In [10]:
coord = [[l.latitude, l.longitude] for l in sahel_coord]

coord[:5]

AttributeError: 'NoneType' object has no attribute 'latitude'

In [11]:
for i in range(len(sahel_coord)):
    if sahel_coord[i] is None:
        print(sahel_locations[i])

Ennedi Est Chad
Ennedi Ouest Chad
Hodh Ech Chargi Mauritania
Akwa lbom Nigeria


In [12]:
coord_list = []

#For the regions that weren't geocoded by geopy I looked up the coordinates on Google maps

for i in range(len(sahel_coord)):
    if sahel_coord[i] is not None:
        coord_list.append((sahel_coord[i].latitude, sahel_coord[i].longitude))
    else:
        if sahel_locations[i] == "Ennedi Est Chad":
            coord_list.append((16.3074676, 22.46964))
        elif sahel_locations[i] == "Ennedi Ouest Chad":
            coord_list.append((18.3247397, 19.250896))
        elif sahel_locations[i] == "Hodh Ech Chargi Mauritania":
            coord_list.append((19.2697034, -9.4929445))
        elif sahel_locations[i] == "Akwa lbom Nigeria":
            coord_list.append((5.0047492, 7.619581))

In [13]:
coord_list[:5]

[(12.4777805, -3.58795703101245),
 (10.30718125, -4.4351892203504),
 (12.36894, -1.5435073646143),
 (11.7337, -0.289661956172839),
 (13.23871, -1.03498305140845)]

In [14]:
set(df_sahel["CNTRY_NAME"])

{u'Burkina Faso',
 u'Cameroon',
 u'Chad',
 u'Gambia',
 u'Mali',
 u'Mauritania',
 u'Niger',
 u'Nigeria',
 u'Senegal'}

In [15]:
map_sahel = folium.Map(location=(17.145087, 3.223233), zoom_start=4)

for i in range(len(coord_list)):
    if df_sahel["CNTRY_NAME"][i] == "Mali":
        map_sahel.simple_marker(coord_list[i], popup="Prevalence of SAM: %.2f" % df_sahel["Latest SAM Prevalence"][i],
                               marker_color="cadetblue")
    elif df_sahel["CNTRY_NAME"][i] == "Mauritania":
        map_sahel.simple_marker(coord_list[i], popup="Prevalence of SAM: %.2f" % df_sahel["Latest SAM Prevalence"][i],
                               marker_color="purple")
    elif df_sahel["CNTRY_NAME"][i] == "Niger":
        map_sahel.simple_marker(coord_list[i], popup="Prevalence of SAM: %.2f" % df_sahel["Latest SAM Prevalence"][i],
                               marker_color="darkpurple")
    elif df_sahel["CNTRY_NAME"][i] == "Senegal":
        map_sahel.simple_marker(coord_list[i], popup="Prevalence of SAM: %.2f" % df_sahel["Latest SAM Prevalence"][i],
                               marker_color="darkred")
    elif df_sahel["CNTRY_NAME"][i] == "Chad":
        map_sahel.simple_marker(coord_list[i], popup="Prevalence of SAM: %.2f" % df_sahel["Latest SAM Prevalence"][i],
                               marker_color="darkblue")
    elif df_sahel["CNTRY_NAME"][i] == "Cameroon":
        map_sahel.simple_marker(coord_list[i], popup="Prevalence of SAM: %.2f" % df_sahel["Latest SAM Prevalence"][i],
                               marker_color="darkgreen")
    elif df_sahel["CNTRY_NAME"][i] == "Burkina Faso":
        map_sahel.simple_marker(coord_list[i], popup="Prevalence of SAM: %.2f" % df_sahel["Latest SAM Prevalence"][i],
                               marker_color="gray")
    elif df_sahel["CNTRY_NAME"][i] == "Gambia":
        map_sahel.simple_marker(coord_list[i], popup="Prevalence of SAM: %.2f" % df_sahel["Latest SAM Prevalence"][i],
                               marker_color="green")
    elif df_sahel["CNTRY_NAME"][i] == "Nigeria":
        map_sahel.simple_marker(coord_list[i], popup="Prevalence of SAM: %.2f" % df_sahel["Latest SAM Prevalence"][i],
                               marker_color="lightgray")

###Prevalence of Severe Acute Malnutrition in Sahel (2013/2014)

In [16]:
map_sahel

In [17]:
map_sahel.create_map(path='sam_sahel_map.html')

### Adding a Choropleth map with administrative boundaries

In [18]:
# Adding Admin. bounderies of level 1 (https://data.hdx.rwlabs.org/dataset/sahel-administrative-boundaries)
sahel_admin1 = "sahel_admin1.geojson"

In [19]:
sahel_test = folium.Map(location=(17.145087, 3.223233), zoom_start=4.5)

sahel_test.geo_json(geo_path = sahel_admin1)

In [20]:
sahel_test

In [63]:
sahel_choro = folium.Map(location=(17.145087, 3.223233), zoom_start=4.5)

sahel_choro.geo_json(geo_path = sahel_admin1,
                    data = df_sahel,
                    columns = ["ADM1_CODE", "Latest SAM Prevalence"],
                    key_on='feature.properties.ADM1_CODE',
                    fill_color = 'YlOrRd', 
                    threshold_scale = [0, 0.5, 1, 1.5, 2],
                    fill_opacity = 0.7, 
                    line_opacity = 0.6,
                    legend_name = 'Prevalence of SAM per admin. regions in Sahel',
                    reset=True)

In [64]:
sahel_choro

In [65]:
sahel_choro.create_map(path='sam_sahel_choromap.html')